In [1]:
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import pandas as pd
import librosa
import IPython.display as ipd
from scipy.fft import fft, ifft, fftfreq
import scipy.signal as sig

In [61]:
file = "static5"

y0, sr = librosa.load(file+"_Scarlett 18i20 3rd Gen Multichannel_capture_AUX0.wav",sr=48000)
y1, sr = librosa.load(file+"_Scarlett 18i20 3rd Gen Multichannel_capture_AUX1.wav",sr=48000)
y2, sr = librosa.load(file+"_Scarlett 18i20 3rd Gen Multichannel_capture_AUX2.wav",sr=48000)
y3, sr = librosa.load(file+"_Scarlett 18i20 3rd Gen Multichannel_capture_AUX3.wav",sr=48000)


In [3]:
y5,sr5 = librosa.load("static2_Scarlett 18i20 3rd Gen Multichannel_capture_AUX0.wav",sr=48000)
y6,sr6 = librosa.load("static2_Scarlett 18i20 3rd Gen Multichannel_capture_AUX1.wav",sr=48000)
y7,sr7 = librosa.load("static2_Scarlett 18i20 3rd Gen Multichannel_capture_AUX2.wav",sr=48000)
y8,sr8 = librosa.load("static2_Scarlett 18i20 3rd Gen Multichannel_capture_AUX3.wav",sr=48000)


In [4]:
t0 = 200000
dt = 5000
data = {
   'time':np.arange(dt),
   'amplitude0':y0[t0:t0+dt],
   'amplitude1':y1[t0:t0+dt],
   'amplitude2':y2[t0:t0+dt],
   'amplitude3':y3[t0:t0+dt],
    'cor02': sig.correlate(y5[t0:t0+dt],y7[t0:t0+dt],mode='same'),
    'cor12': sig.correlate(y6[t0:t0+dt],y7[t0:t0+dt],mode='same'),
    'cor01': sig.correlate(y5[t0:t0+dt],y6[t0:t0+dt],mode='same'),
    'cor00': sig.correlate(y5[t0:t0+dt],y7[t0:t0+dt],mode='same')

}
df = pd.DataFrame(data)

In [5]:
def equalize(signal):
    ft = fft(signal)
    eq_ft = []
    for i in ft:
        if abs(i) > 1e-10:
            eq_ft.append(i/abs(i))
        else:
            eq_ft.append(0)
    return(np.real(ifft(eq_ft)))

In [6]:
def first_moment(x,y):
    return sum(x*y)/sum(y)

In [66]:
def select_peak(y,threshhold=.5,exp_width=2000):
    y = y[len(y)//2-exp_width//2:len(y)//2+exp_width//2]
    peakheight = np.max(y)
    max_arg = np.argmax(y)
    relheights = y/peakheight
    lower = np.where(relheights < threshhold)[0]
    lowerleft = lower[lower<max_arg]
    lowerright = lower[lower>max_arg]
    if len(lowerleft) == 0:
        left = 0
    else:
        left = np.max(lower[lower<max_arg])
    if len(lowerright) == 0:
        right = exp_width
    else:
        right = np.min(lower[lower>max_arg])
        
    peakargs = len(y)//2-exp_width//2+np.array(range(left,right))
    return peakargs,y[peakargs]

def smoothe(y,window=2):
    res = np.array(y)
    for i in range(1,window+1):
        res += np.roll(y,i)
        res += np.roll(y,-i)
    return res/(2*window+1)

def peak_cross(signal1,signal2,mode='moment'):
    if mode == 'moment':
        cor = sig.correlate(signal1,signal2,mode='same')
        x,y = select_peak(cor,0.5)
        d = sum(x*y)/sum(y)
        return 1000-d
    elif mode == 'simple':
        cor = sig.correlate(signal1,signal2,mode='same')
        return len(signal1)//2-np.argmax(cor)
    elif mode == 'moment2':
        cor = sig.correlate(signal1,signal2,mode='same')
        cor_reduced = cor[len(signal1)//2-200:len(signal1)//2+200]
        rough_estimate = len(signal1)//2-200+np.argmax(cor_reduced)
        finer_estimate = first_moment(np.arange(rough_estimate-20,rough_estimate+20),cor[rough_estimate-20:rough_estimate+20])
        return len(signal1)//2-finer_estimate

In [28]:
t0 = 300000
dt = 5000
data = {
   'time':np.arange(dt),
   'amplitude0':y5[t0:t0+dt],
   'amplitude1':y6[t0:t0+dt],
   'amplitude2':y7[t0:t0+dt],
   'amplitude3':y8[t0:t0+dt],
    'cor02': sig.correlate(y5[t0:t0+dt],y7[t0:t0+dt],mode='same'),
    'cor12': sig.correlate(y6[t0:t0+dt],y7[t0:t0+dt],mode='same'),
    'cor01': sig.correlate(y5[t0:t0+dt],y6[t0:t0+dt],mode='same'),
    'cor00': sig.correlate(y5[t0:t0+dt],y5[t0:t0+dt],mode='same')

}
df = pd.DataFrame(data)

In [29]:
cor02 = sig.correlate(df['amplitude0'],df['amplitude2'],mode='same')
cor02_norm = sig.correlate(df['amplitude0']/max(df['amplitude0']),df['amplitude2']/max(df['amplitude2']),mode='same')
fig = px.line(cor02/max(cor02))
fig.add_scatter(y=cor02_norm/max(cor02_norm))
#fig.add_scatter(y=df['cor12'])

#fig.add_scatter(y=df['cor00'])
fig.show()

In [10]:
peakx, peaky = select_peak(smoothe(cor,100),.1)
px.line(x=peakx,y=peaky)

NameError: name 'cor' is not defined

In [330]:
ipd.Audio(y7,rate=sr5)

In [339]:
y, sr = librosa.load("mic_pos.wav",sr=48000,mono=False)


In [343]:
ipd.Audio(y[1],rate=sr)

In [13]:
i = 157
t0 = 100000+i*1000
dt = 20000
data = {
   'time':np.arange(dt),
   'amplitude0':y0[t0:t0+dt],
   'amplitude1':y1[t0:t0+dt],
   'amplitude2':y2[t0:t0+dt],
   'amplitude3':y3[t0:t0+dt]
}
df = pd.DataFrame(data)

In [12]:
fig = px.line(sig.correlate(df['amplitude0'],df['amplitude1'],mode='same'))
fig.add_scatter(y=sig.correlate(df['amplitude1'],df['amplitude2'],mode='same'))
fig.add_scatter(y=sig.correlate(df['amplitude0'],df['amplitude2'],mode='same'))


In [163]:
n = 1
display(peak_cross(df['amplitude0']**n,df['amplitude1']**n)+peak_cross(df['amplitude1']**n,df['amplitude2']**n),peak_cross(df['amplitude0']**n,df['amplitude2']**n))

5.8934620499567245

-18.449913352249496

In [63]:
N = 200
errors = np.zeros(N)
errors2 = np.zeros(N)
errors3 = np.zeros(N)

for i in range(N):
    t0 = i*48000//20
    dt = 5000
    data = {
       'time':np.arange(dt),
       'amplitude0':equalize(y0[t0:t0+dt]),
       'amplitude1':equalize(y1[t0:t0+dt]),
       'amplitude2':equalize(y2[t0:t0+dt]),
       'amplitude3':equalize(y3[t0:t0+dt])
    }
    df = pd.DataFrame(data)
    errors[i] = peak_cross(df['amplitude0'],df['amplitude1'])+peak_cross(df['amplitude1'],df['amplitude2'])-peak_cross(df['amplitude0'],df['amplitude2'])
    errors2[i] = peak_cross(df['amplitude0'],df['amplitude3'])+peak_cross(df['amplitude3'],df['amplitude2'])-peak_cross(df['amplitude0'],df['amplitude2'])
    errors3[i] = peak_cross(df['amplitude1'],df['amplitude3'])+peak_cross(df['amplitude3'],df['amplitude2'])-peak_cross(df['amplitude1'],df['amplitude2'])

In [67]:
N = 200
errors = np.zeros(N)
errors2 = np.zeros(N)
errors3 = np.zeros(N)

for i in range(N):
    t0 = i*48000//20
    dt = 5000
    data = {
       'time':np.arange(dt),
       'amplitude0':y0[t0:t0+dt],
       'amplitude1':y1[t0:t0+dt],
       'amplitude2':y2[t0:t0+dt],
       'amplitude3':y3[t0:t0+dt]
    }
    df = pd.DataFrame(data)
    errors[i] = peak_cross(df['amplitude0'],df['amplitude1'])+peak_cross(df['amplitude1'],df['amplitude2'])-peak_cross(df['amplitude0'],df['amplitude2'])
    errors2[i] = peak_cross(df['amplitude0'],df['amplitude3'])+peak_cross(df['amplitude3'],df['amplitude2'])-peak_cross(df['amplitude0'],df['amplitude2'])
    errors3[i] = peak_cross(df['amplitude1'],df['amplitude3'])+peak_cross(df['amplitude3'],df['amplitude2'])-peak_cross(df['amplitude1'],df['amplitude2'])

In [68]:
data = {
   'time (s)':np.arange(N)/20,
   'error (ms)':errors/48,
}
df = pd.DataFrame(data)

In [70]:
fig = px.line(df,x="time (s)",y="error (ms)")
fig.update_layout(
    title = "Moment Detection",
    font_family="Times New Roman",
    font_color="black",
    font_size=25,
    autosize=False,
    width=600,
    height=600,
    showlegend=False,yaxis_range=[-10,10])
fig.show()

In [71]:
5000/48000

0.10416666666666667

In [71]:
np.arange(5,10)

array([5, 6, 7, 8, 9])

In [94]:
len(y5)

566513